<a href="https://colab.research.google.com/github/Prajwal011/LLM-s/blob/main/Text_to_speech_using_LLM's.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip  install -q -U datasets peft transformers diffusers accelerate xformers langchain-text-splitters TTS

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 kB 5.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 76.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.6/101.6 kB 7.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.3/15.3 MB 88.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.1/18.1 MB 22.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 12.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.9/10.9 MB 91.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 938.0/938.0 kB 46.4 MB

In [ ]:
from IPython.display import Audio
from transformers import pipeline
import numpy as np
from langchain_text_splitters import RecursiveCharacterTextSplitter
from transformers import pipeline
from datasets import load_dataset
import torch

talk='''
John: Hey Sarah, have you heard about Large Language Models like GPT-4?

Sarah: Yes, I have! They're quite fascinating. I know they can generate human-like text. But I'm not entirely clear on how they work. Can you explain?

John: Absolutely. Large Language Models, or LLMs, are a type of artificial intelligence that can understand and generate text. They are trained on vast amounts of data from the internet to learn the patterns and structures of human language.

Sarah: So, they basically learn from all the text data they are fed?
'''

rt = RecursiveCharacterTextSplitter(separators='\n',chunk_size=100,chunk_overlap=00,)
docs = rt.split_text(talk)
docs

['John: Hey Sarah, have you heard about Large Language Models like GPT-4?',
 "\nSarah: Yes, I have! They're quite fascinating. I know they can generate human-like text. But I'm not entirely clear on how they work. Can you explain?",
 '\nJohn: Absolutely. Large Language Models, or LLMs, are a type of artificial intelligence that can understand and generate text. They are trained on vast amounts of data from the internet to learn the patterns and structures of human language.',
 'Sarah: So, they basically learn from all the text data they are fed?']

### bark suno-ai

In [ ]:
synthesizer = pipeline("text-to-speech", "suno/bark",device='cuda')

audio_all = np.array([])
for i in docs:
  speech = synthesizer(i)
  audio_all =  np.concatenate((audio_all,speech['audio']),axis = None)


In [ ]:
Audio(audio_all,rate=15900)

### microsoft tts model

In [ ]:
synthesiser = pipeline("text-to-speech", "microsoft/speecht5_tts",device='cuda')
embeddings_dataset = load_dataset("Matthijs/cmu-arctic-xvectors", split="validation")
speaker_embedding = torch.tensor(embeddings_dataset[7306]["xvector"]).unsqueeze(0)

audio_all = np.array([])
for i in docs:
  speech = synthesiser(i, forward_params={"speaker_embeddings": speaker_embedding})
  audio_all =  np.concatenate((audio_all,speech['audio']),axis = None)


In [ ]:
Audio(audio_all,rate=15000)

### TTS library python

In [ ]:
from TTS.api import TTS
tts = TTS("tts_models/multilingual/multi-dataset/xtts_v2" ,gpu=True)

tts.tts_to_file(text=talk,
                file_path="output.wav",
                speaker_wav="/content/Standard recording 1.wav",
                language="en")

 > tts_models/multilingual/multi-dataset/xtts_v2 is already downloaded.
 > Using model: xtts
 > Text splitted to sentences.
['John: Hey Sarah, have you heard about Large Language Models like GPT-4?', 'Sarah: Yes, I have!', "They're quite fascinating.", 'I know they can generate human-like text.', "But I'm not entirely clear on how they work.", 'Can you explain?', 'John: Absolutely.', 'Large Language Models, or LLMs, are a type of artificial intelligence that can understand and generate text.', 'They are trained on vast amounts of data from the internet to learn the patterns and structures of human language.', 'Sarah: So, they basically learn from all the text data they are fed?']
 > Processing time: 320.967405796051
 > Real-time factor: 5.425404220687879


'output.wav'

In [ ]:
Audio('output.wav')